In [1]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
from itables import show
import os
import glob
import matplotlib.pyplot as plt
from tqdm.auto import tqdm
tqdm.pandas()
import json
files = sorted(glob.glob("data/hydrated/climate_tweets_*.jsonl"))
print(files)
pd.set_option("display.max_colwidth", None)
pd.set_option("display.max_columns", None)

<IPython.core.display.Javascript object>

['data/hydrated/climate_tweets_2006.jsonl', 'data/hydrated/climate_tweets_2007.jsonl', 'data/hydrated/climate_tweets_2008.jsonl', 'data/hydrated/climate_tweets_2009.jsonl', 'data/hydrated/climate_tweets_2010.jsonl', 'data/hydrated/climate_tweets_2011.jsonl', 'data/hydrated/climate_tweets_2012.jsonl', 'data/hydrated/climate_tweets_2013.jsonl', 'data/hydrated/climate_tweets_2014.jsonl', 'data/hydrated/climate_tweets_2015.jsonl', 'data/hydrated/climate_tweets_2016.jsonl', 'data/hydrated/climate_tweets_2017.jsonl', 'data/hydrated/climate_tweets_2018.jsonl', 'data/hydrated/climate_tweets_2019.jsonl', 'data/hydrated/climate_tweets_2020.jsonl']


In [2]:
# To pretty print a tweet JSON:
#! tail -n 1 data/hydrated/climate_tweets_2020.jsonl | python -m json.tool

In [3]:
filename = "data/geotagged_climate_tweets.csv"
if os.path.isfile(filename):
    # Load cached filtered data
    df = pd.read_csv(filename, lineterminator="\n")
else:
    # Filter the dataset for tweets that are geotagged
    has_geotag = []
    for filename in tqdm(files):
        with tqdm(total = os.path.getsize(filename)) as pbar:
            with open(filename, "r") as file:
                for line in file:
                    pbar.update(len(line))
                    row = json.loads(line)
                    if row["coordinates"] or row["place"]:
                        has_geotag.append(row)
    print(len(has_geotag))
    df = pd.DataFrame(has_geotag)
    df.to_csv(filename, index=False)

/usr/local/lib/python3.6/dist-packages/IPython/core/interactiveshell.py:3072: DtypeWarning: Columns (28,29,30,31,32,33) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [4]:
df.created_at = pd.to_datetime(df.created_at)
df.index = df.created_at

In [5]:
df.coordinates = df.coordinates.apply(lambda x: eval(x) if type(x) == str else None)
df.place = df.place.apply(lambda x: eval(x) if type(x) == str else None)

In [6]:
# Tweets with an exact latlong
df_coords = df[~pd.isna(df.coordinates)].copy()
df_coords["longitude"] = df_coords.coordinates.apply(lambda x: x["coordinates"][0])
df_coords["latitude"] = df_coords.coordinates.apply(lambda x: x["coordinates"][1])
df_coords[["latitude", "longitude"]].to_csv("climate_tweet_latlngs.csv")
print(len(df_coords))

108032


In [7]:
import folium
from folium.plugins import HeatMap, HeatMapWithTime

map = folium.Map(location = [0,0], zoom_start = 2)
HeatMap(df_coords[["latitude", "longitude"]]).add_to(map)
map.save("climate_tweet_heatmap.html")
map

In [8]:
df_coords.created_at.describe()

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:1: FutureWarning: Treating datetime data as categorical rather than numeric in `.describe` is deprecated and will be removed in a future version of pandas. Specify `datetime_is_numeric=True` to silence this warning and adopt the future behavior now.
  """Entry point for launching an IPython kernel.


count                        108032
unique                       107311
top       2011-07-24 06:13:06+00:00
freq                              6
first     2010-09-11 04:56:01+00:00
last      2020-08-10 23:53:13+00:00
Name: created_at, dtype: object

In [9]:
map = folium.Map(location = [0,0], zoom_start = 2)
data_by_year = []
time_range = list(range(2010, 2021))
for year in time_range:
    data_by_year.append(df_coords[["latitude","longitude"]][df_coords.index.year == year].values.tolist())
HeatMapWithTime(
    data_by_year,
    index = time_range,
    auto_play = True,
    #max_opacity = 0.3
).add_to(map)
map.save("climate_tweet_heatmap_by_year.html")
map

In [10]:
df.columns

Index(['created_at', 'id', 'id_str', 'full_text', 'truncated',
       'display_text_range', 'entities', 'source', 'in_reply_to_status_id',
       'in_reply_to_status_id_str', 'in_reply_to_user_id',
       'in_reply_to_user_id_str', 'in_reply_to_screen_name', 'user', 'geo',
       'coordinates', 'place', 'contributors', 'is_quote_status',
       'retweet_count', 'favorite_count', 'favorited', 'retweeted', 'lang',
       'possibly_sensitive', 'extended_entities', 'quoted_status_id',
       'quoted_status_id_str', 'quoted_status_permalink', 'quoted_status',
       'withheld_in_countries', 'scopes', 'withheld_scope',
       'withheld_copyright'],
      dtype='object')

In [11]:
# Tweets with exact coordinates, but no geocoded city name - failed to geocode ocean points?
df[["coordinates", "place"]][~pd.isna(df.coordinates) & pd.isna(df.place)]

coordinates  \
created_at                                                                                  
2010-09-19 23:42:58+00:00       {'type': 'Point', 'coordinates': [-92.334656, 38.944393]}   
2010-09-19 22:40:28+00:00  {'type': 'Point', 'coordinates': [-122.29492095, 47.69044571]}   
2010-09-19 22:53:49+00:00       {'type': 'Point', 'coordinates': [119.447079, -5.149646]}   
2010-09-19 21:44:44+00:00        {'type': 'Point', 'coordinates': [-112.00476, 33.43545]}   
2010-09-19 10:51:35+00:00        {'type': 'Point', 'coordinates': [106.97349, -6.257013]}   
...                                                                                   ...   
2020-01-17 17:07:50+00:00              {'type': 'Point', 'coordinates': [-1.93765402, 0]}   
2020-01-12 20:40:02+00:00    {'type': 'Point', 'coordinates': [-33.11987861, 4.20525135]}   
2020-01-06 11:51:41+00:00      {'type': 'Point', 'coordinates': [0.00017874, -3.055e-05]}   
2020-01-04 06:04:03+00:00             {'type': 'Point', 'coordinates': [-119.2953186, 0]}   
2020-01-03 17:30:03+00:00   {'type': 'Point', 'coordinates': [70.06122585, -59.63917586]}   

                          place  
created_at                       
2010-09-19 23:42:58+00:00  None  
2010-09-19 22:40:28+00:00  None  
2010-09-19 22:53:49+00:00  None  
2010-09-19 21:44:44+00:00  None  
2010-09-19 10:51:35+00:00  None  
...                         ...  
2020-01-17 17:07:50+00:00  None  
2020-01-12 20:40:02+00:00  None  
2020-01-06 11:51:41+00:00  None  
2020-01-04 06:04:03+00:00  None  
2020-01-03 17:30:03+00:00  None  

[9179 rows x 2 columns]

In [12]:
print(len(df))
print(sum(~pd.isna(df.place)))

778201
769022


In [13]:
# Extract city information from place column
df["city_full_name"] = df.place.apply(lambda p: p["full_name"] if p else None)
df["city_name"] = df.place.apply(lambda p: p["name"] if p else None)
df["country"] = df.place.apply(lambda p: p["country"] if p else None)
df["country_code"] = df.place.apply(lambda p: p["country_code"] if p else None)

In [14]:
tweets_by_city = df.city_full_name.value_counts()
tweets_by_city.head()

Melbourne, Victoria        17539
Manhattan, NY              13919
Sydney, New South Wales    12557
Washington, DC             10680
Los Angeles, CA            10303
Name: city_full_name, dtype: int64

In [15]:
df.country.value_counts().head()

United States     394180
United Kingdom     88817
Australia          57952
Canada             55015
India              18928
Name: country, dtype: int64

In [16]:
fields = []
with open("data/geonames/fields.txt", "r") as f:
    for line in f:
        fields.append(line.split(":")[0].strip())
cities = pd.read_table("data/geonames/cities500.txt", names=fields, low_memory=False)

In [17]:
cities[["name", "country code", "latitude", "longitude", "population"]].sort_values(by="population", ascending=False).head(15)

name country code  latitude  longitude  population
23069       Shanghai           CN  31.22222  121.45806    22315474
169455      Istanbul           TR  41.01384   28.94966    14804116
1359    Buenos Aires           AR -34.61315  -58.37723    13076300
98464         Mumbai           IN  19.07283   72.88261    12691836
119675   Mexico City           MX  19.42847  -99.12766    12294193
26959        Beijing           CN  39.90750  116.39723    11716620
145123       Karachi           PK  24.86080   67.01040    11624219
22403        Tianjin           CN  39.14222  117.17667    11090314
25686      Guangzhou           CN  23.11667  113.25000    11071424
98246          Delhi           IN  28.65195   77.23149    10927986
160110        Moscow           RU  55.75222   37.61556    10381222
22931       Shenzhen           CN  22.54554  114.06830    10358381
10549          Dhaka           BD  23.71040   90.40744    10356500
113554         Seoul           KR  37.56600  126.97840    10349312
14271      São Paulo           BR -23.54750  -46.63611    10021295

In [18]:
cities[cities.name == "Canberra"]

geonameid      name asciiname  \
7042    2172517  Canberra  Canberra   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               alternatenames  \
7042  CBR,Camberra,Canberra,Canberrah,Kamberra,Kambra,Kampera,Kanapera,Kanbera,Kanbero,Kanberr,Kanberra,Kanberrae,Kanberre,Kanbérra,Kham-phi-la,Khâm-phì-là,Kānapera,kaenbeola,kainabara,kainberra,kan pei la,kanabera,kanbra,kanpara,kenabera,kyanabara,kyanabera,kyanbera,kynbra,kʼanbera,qnbrh,Καμπέρα,Канбера,Канберрæ,Канберра,Канберре,Канбєра,Կանբերրա,קאנבערא,קנברה,كانبرا,کانبرا,کانبێرا,کینبرا,कॅनबेरा,कैनबरा,कैन्बेर्रा,क्यानबरा,ক্যানবেরা,ਕੈਨਬਰਾ,କାନବେରା,கான்பரா,കാൻബറ,කැන්බරා,แคนเบอร์รา,ཁན་པེ་ར།,კანბერა,ካንበራ,キャンベラ,坎培拉,堪培拉,캔버라   

      latitude  longitude feature class feature code country code  cc2  \
7042 -35.28346  149.12807             P         PPLC           AU  NaN   

     admin1 code admin2 code admin3 code admin4 code  population  elevation  \
7042          01         NaN         NaN         NaN      367752        NaN   

      dem          timezone modification date  
7042  571  Australia/Sydney        2019-09-05